# Exploration

## Import

In [13]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from scipy.stats import gaussian_kde

## Data Processing

In [49]:
# Read the txt file (change the filename to yours)
data = np.loadtxt("data/rec0035_raw_audio_peak_target_points.txt")

# Reshape into columns of 3 (x, y, z)
points = data.reshape(-1, 3)

# Create a dataframe for clarity
df = pd.DataFrame(points, columns=["X", "Y", "Z"])

df.head()

X         Y         Z
0  0.272683 -1.991065  7.433122
1 -0.627328 -2.277209  7.328763
2 -1.741731  0.240967  7.496553
3 -1.886049 -1.337800  7.344597
4  2.083748  0.238148  7.408865

### Visualizing the data points

Let's first visualize the points in a 3D space.

In [47]:
fig = go.Figure(data=[go.Scatter3d(
    x=df["X"], y=df["Y"], z=df["Z"],
    mode='markers',
    marker=dict(
        size=3,
        opacity=0.7
    )
)])

fig.update_layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z'
    ),
    title="3D Acoustic Points Visualization"
)

fig.show()

### Density map
Using a density map we can easily visualize the distribution of the data and where the most points are located.

In [ ]:

## Calculating the KDE density
xyz = np.vstack([df["X"], df["Y"], df["Z"]])
kde = gaussian_kde(xyz, bw_method=0.2)

# Creating the grid in the space
x_range = np.linspace(df["X"].min(), df["X"].max(), 50)
y_range = np.linspace(df["Y"].min(), df["Y"].max(), 50)
z_range = np.linspace(0, 10, 50)
xx, yy, zz = np.meshgrid(x_range, y_range, z_range)
coords = np.vstack([xx.ravel(), yy.ravel(), zz.ravel()])

## Getting the estimated density for each point in the grid space
density = kde(coords).reshape(xx.shape)


In [42]:

fig = go.Figure(data=go.Volume(
    x=xx.flatten(),
    y=yy.flatten(),
    z=zz.flatten(),
    value=density.flatten(),
    isomin=np.quantile(density, 0.95), # Specify the minimum value for the density getting the quantile 95
    isomax=density.max(),
    opacity=0.20,  # lower = more transparent
    surface_count=15,  # number of contour layers
    colorscale='Inferno' 
))

fig.update_layout(
    scene=dict(
        xaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        yaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        zaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black', range=[0,10]),
    ),
    title="3D Density Heatmap of Acoustic Points"
)

fig.show()

### High Density Identification
We can identify where the high density is by counting the number of point in a predefined cube space.
We can bin the space into a grid and count the number of points in each bin.

In [43]:
cube_size = 0.5  # Cube dimensions

# Identifying the bin where each point belongs to
df["X_bin"] = np.floor(df["X"] / cube_size).astype(float)
df["Y_bin"] = np.floor(df["Y"] / cube_size).astype(float)
df["Z_bin"] = np.floor(df["Z"] / cube_size).astype(float)

# Count the number of points in each bin
cube_counts = (
    df.groupby(["X_bin", "Y_bin", "Z_bin"])
    .size()
    .reset_index(name="count")
)

# Getting the bin with the most points, this is the densest cube
max_cube = cube_counts.loc[cube_counts["count"].idxmax()]
x_bin, y_bin, z_bin = max_cube[["X_bin", "Y_bin", "Z_bin"]]
print(f"Most dense cube origin: ({x_bin}, {y_bin}, {z_bin}) — count = {max_cube['count']}")


Most dense cube origin: (-4.0, -3.0, 14.0) — count = 8.0


In [44]:
# Getting the coordinates of the cube
x0, y0, z0 = x_bin * cube_size, y_bin * cube_size, z_bin * cube_size
x1, y1, z1 = x0 + cube_size, y0 + cube_size, z0 + cube_size

# Getting the points inside the cube
inside = df[
    (df["X"] >= x0) & (df["X"] < x1) &
    (df["Y"] >= y0) & (df["Y"] < y1) &
    (df["Z"] >= z0) & (df["Z"] < z1)
]

In [45]:
fig = go.Figure()

# Plot all points (light gray)
fig.add_trace(go.Scatter3d(
    x=df["X"], y=df["Y"], z=df["Z"],
    mode='markers',
    marker=dict(size=3, color='lightgray', opacity=0.3),
    name="All Points"
))

# Highlight points inside the high-density cube (red)
fig.add_trace(go.Scatter3d(
    x=inside["X"], y=inside["Y"], z=inside["Z"],
    mode='markers',
    marker=dict(size=5, color='red'),
    name="Points in High-Density Cube"
))

# Draw the cube as a wireframe
fig.add_trace(go.Mesh3d(
    x=[x0, x1, x1, x0, x0, x1, x1, x0],
    y=[y0, y0, y1, y1, y0, y0, y1, y1],
    z=[z0, z0, z0, z0, z1, z1, z1, z1],
    color='red',
    opacity=0.2,
    alphahull=0,
    name="High-Density Cube"
))

fig.update_layout(
    scene=dict(
        xaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        yaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black'),
        zaxis=dict(showbackground=False, showgrid=False, showline=True, linecolor='black', range=[0,10]),
    ),
    title="Cube with Highest Point Density"
)

fig.show()